In [1]:
import os
os.environ["KERAS_BACKEND"] = "tensorflow"
import keras
from keras import layers
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Conv2D, Flatten, Dense
from gymnasium.wrappers import FrameStack
from gymnasium.experimental.wrappers import GrayscaleObservationV0
import gymnasium as gym
import numpy as np
import tensorflow as tf

In [2]:
env = gym.make('ALE/Frogger-v5') # Human render mode slows things down A LOT

In [3]:
env = GrayscaleObservationV0(env) # Remove RGB channels (make gray) in order to decrease amount of data to process
env.observation_space.shape

(210, 160)

In [4]:
seed = 42 # Allows us to repeat the same patterns of game play
env = FrameStack(env, 4) # Get 4 frames from game at a time
frames, width, height = env.observation_space.shape
env.seed(seed)

C:\Users\ethan\anaconda3\Lib\site-packages\gymnasium\core.py:311: UserWarning: WARN: env.seed to get variables from other wrappers is deprecated and will be removed in v1.0, to get this variable you can do `env.unwrapped.seed` for environment variables or `env.get_wrapper_attr('seed')` that will search the reminding wrappers.
  logger.warn(


(3444837047, 2669555309)

In [5]:
print(frames,width,height)

4 210 160


In [6]:
# This network learns an approximation of the Q-table, which is a mapping between the states and actions that an agent will take. 
# For every state we'll have FIVE actions that can be taken (NOOP, Up, Down, Left, Right). 
# The environment provides the state, and the action is chosen by selecting the largest of the five Q-values predicted in the output layer of the CNN.

num_actions = 5

# three convolution and three dense layers
def create_CNN():
    model = Sequential()
    
    model.add(Conv2D(32, (8, 8), strides=(4, 4), padding='same', activation='relu', input_shape=(4, 210, 160)))
    model.add(Conv2D(64, (4, 4), strides=(2, 2), padding='same', activation='relu'))
    
    model.add(Flatten())
    
    model.add(Dense(32, activation='relu'))
    model.add(Dense(num_actions, activation='linear'))
    return model

In [7]:
# The first neural net makes the predictions for Q-values, which are used to take an action.
cnn1 = create_CNN()
if os.path.exists('cnn1v2.weights.h5'):
    cnn1.load_weights("cnn1v2.weights.h5")

# A second cnn is used to predict future rewards. The weights of the second cnn get updated every 10000 steps.
cnn2 = create_CNN()
if os.path.exists('cnn2v2.weights.h5'):
    cnn1.load_weights("cnn2v2.weights.h5")

C:\Users\ethan\anaconda3\Lib\site-packages\keras\src\layers\convolutional\base_conv.py:107: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


In [10]:
# Hyperparamaters DQN Algorithm

gamma = 0.99  # Discount factor in Bellman's equuation
epsilon = 1  # Epsilon greedy parameter for Q learning algorithm
max_steps_per_episode = 75 #Deepmind trained for "a total of 50 million frames (~38 days of game play)"
max_episodes = 5000  # Number of episodes you let the AI train. Keep above 1!
epsilon_min = 0.1  # Smallest epsilon value possible
epsilon_max = 1.0  # Largest epsilon value possible
epsilon_interval = (epsilon_max - epsilon_min)  # Rate we reduce chance of random action being taken (eventually, we don't want to take many random actions)

# Somre more important variables
batch_size = 32  # Size of sample taken from "replay buffer"
optimizer = keras.optimizers.Adam(learning_rate=0.00025, clipnorm=1.0)

# Experience replay buffers
action_history = []
state_history = []
state_next_history = []
rewards_history = []
done_history = []
episode_reward_history = []
running_reward = 0
episode_count = 0
frame_count = 0
# Number of frames to take random action and observe output
epsilon_random_frames = 100000
# Number of frames for exploration
epsilon_greedy_frames = 1000000.0
# Maximum replay length
# Note: A Deepmind paper suggests 1000000, however this can cause memory issues
max_memory_length = 100000
# Train the model after 4 actions
update_after_actions = 4
# How often to update cnn2
update_cnn2 = 10000
# Using huber loss to check for convergance of Qs
loss_function = keras.losses.Huber()

In [ ]:
stepcount=0


# DQN Algorithm
while True:
    observation, _ = env.reset()
    state = np.array(observation)
    episode_reward = 0
    totalSteps = 0
    
    for timestep in range(1, max_steps_per_episode):
        frame_count += 1
        # Use epsilon-greedy policy to explore or exploit
            # If current frame_count is less than 50,000 or epsilon is greater than a random number between 0 and 1
        print("Frame Count: ", frame_count)
        if frame_count < epsilon_random_frames or epsilon > np.random.rand(1)[0]:
            # Take random action
            action = np.random.choice(num_actions)
        else:
            # Predict Q-values from environment state
            state_tensor = keras.ops.convert_to_tensor(state) # Turn state (frame in game) into a Tensor Object (think matrix)
            state_tensor = keras.ops.expand_dims(state_tensor, 0) # Add to the current batch
            action_probs = cnn1(state_tensor, training=False)
            print(action_probs)
            # Take best action
            action = keras.ops.argmax(action_probs[0]).numpy()
        
        # Decrease probability of taking random action
        epsilon -= epsilon_interval / epsilon_greedy_frames
        epsilon = max(epsilon, epsilon_min)
        
        # Take action in environment
        print("Action: ", action)
        state_next, reward, done, _, _ = env.step(action)
        state_next = np.array(state_next)
        
        # Sum rewards across entire episode
        totalSteps += 1
        episode_reward += reward

        # Save actions and states in "replay buffer"
        action_history.append(action)
        state_history.append(state)
        state_next_history.append(state_next)
        done_history.append(done)
        rewards_history.append(reward)
        state = state_next
        
        # Update every fourth frame AND once batch size is greater than 32
        if frame_count % update_after_actions == 0 and len(done_history) > batch_size:
            # Get indices of samples for replay buffers
            indices = np.random.choice(range(len(done_history)), size=batch_size)

            # Using list comprehension to sample from replay buffer
            state_sample = np.array([state_history[i] for i in indices])
            state_next_sample = np.array([state_next_history[i] for i in indices])
            rewards_sample = [rewards_history[i] for i in indices]
            action_sample = [action_history[i] for i in indices]
            done_sample = keras.ops.convert_to_tensor(
                [float(done_history[i]) for i in indices]
            )

            # Build the updated Q-values for the sampled future states using cnn2
            future_rewards = cnn2.predict(state_next_sample)
            # Q value = reward + discount factor * expected future reward (Bellman's Equation)
            updated_q_values = rewards_sample + gamma * keras.ops.amax(future_rewards, axis=1)

            # If final frame set the last value to -1
            updated_q_values = updated_q_values * (1 - done_sample) - done_sample

            # Create a 'mask' (matrix of 0s and 1s) so we only calculate loss on the updated Q-values
            masks = keras.ops.one_hot(action_sample, num_actions)
            
            # Train the cnn1 using updated Q-values
            with tf.GradientTape() as tape:
                q_values = cnn1(state_sample)

                # Apply the masks to the Q-values to get the Q-value for action taken
                q_action = keras.ops.sum(keras.ops.multiply(q_values, masks), axis=1)
                # Calculate loss between new Q-value and old Q-value
                loss = loss_function(updated_q_values, q_action)

            # Backpropagation - how cnn1 is updated
            grads = tape.gradient(loss, cnn1.trainable_variables)
            optimizer.apply_gradients(zip(grads, cnn1.trainable_variables))
        
        # Time to update cnn2?
        if frame_count % update_cnn2 == 0:
            # update cnn2 with new weights
            cnn2.set_weights(cnn1.get_weights())
            # Log details
            template = "running reward: {:.2f} at episode {}, frame count {}"
            #print(template.format(running_reward, episode_count, frame_count))

        # Limit the state and reward history
        if len(rewards_history) > max_memory_length:
            del rewards_history[:1]
            del state_history[:1]
            del state_next_history[:1]
            del action_history[:1]
            del done_history[:1]

        if done:
            print("DONE")
            break

    # Update running reward to check condition for solving
    s = episode_reward
    x = totalSteps
    actualScore = abs(10*(s/(x-(1.75*s))))
    
    if actualScore > s:
        actualScore = s
    
    episode_reward_history.append(actualScore)
    if len(episode_reward_history) > 100:
        del episode_reward_history[:1]
    
    running_reward = np.mean(episode_reward_history)
    print("Average Reward Across All Episodes: ", running_reward)
    episode_count += 1

    if running_reward > 40:  # Condition to consider game "learned"
        print("Learned at episode {}!".format(episode_count))
        break

    if (max_episodes > 0 and episode_count >= max_episodes):  # Maximum number of episodes reached
        print("Stopped at episode {}!".format(episode_count))
        break
        
    if stepcount<200:
        stepcount+=1
    else:
        stepcount=0

Frame Count:  1
Action:  1
Frame Count:  2
Action:  3
Frame Count:  3
Action:  3
Frame Count:  4
Action:  2
Frame Count:  5
Action:  3
Frame Count:  6
Action:  1
Frame Count:  7
Action:  4
Frame Count:  8
Action:  2
Frame Count:  9
Action:  2
Frame Count:  10
Action:  1
Frame Count:  11
Action:  3
Frame Count:  12
Action:  1
Frame Count:  13
Action:  1
Frame Count:  14
Action:  4
Frame Count:  15
Action:  4
Frame Count:  16
Action:  3
Frame Count:  17
Action:  1
Frame Count:  18
Action:  2
Frame Count:  19
Action:  4
Frame Count:  20
Action:  4
Frame Count:  21
Action:  0
Frame Count:  22
Action:  3
Frame Count:  23
Action:  3
Frame Count:  24
Action:  0
Frame Count:  25
Action:  3
Frame Count:  26
Action:  4
Frame Count:  27
Action:  3
Frame Count:  28
Action:  3
Frame Count:  29
Action:  2
Frame Count:  30
Action:  3
Frame Count:  31
Action:  4
Frame Count:  32
Action:  2
Frame Count:  33
Action:  4
Frame Count:  34
Action:  4
Frame Count:  35
Action:  4
Frame Count:  36
Action:  0
1

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 21ms/step
Frame Count:  189
Action:  2
Frame Count:  190
Action:  4
Frame Count:  191
Action:  4
Frame Count:  192
Action:  2
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step
Frame Count:  193
Action:  4
Frame Count:  194
Action:  3
Frame Count:  195
Action:  1
Frame Count:  196
Action:  2
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
Frame Count:  197
Action:  4
Frame Count:  198
Action:  3
Frame Count:  199
Action:  1
Frame Count:  200
Action:  1
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 27ms/step
Frame Count:  201
Action:  3
Frame Count:  202
Action:  2
Frame Count:  203
Action:  4
Frame Count:  204
Action:  0
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 13ms/step
Frame Count:  205
Action:  4
Frame Count:  206
Action:  4
Frame Count:  207
Action:  0
Frame Count:  208
Action:  4
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 28ms/step
Frame Count:  209
Action:  2
Frame Count:  210
Action:  2
Frame Count:  211
Action:  4
Frame Count:  212
Action:  0
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
Frame Count:  213
Action:  1
Frame Cou

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
Frame Count:  361
Action:  2
Frame Count:  362
Action:  2
Frame Count:  363
Action:  2
Frame Count:  364
Action:  2
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 22ms/step
Frame Count:  365
Action:  2
Frame Count:  366
Action:  0
Frame Count:  367
Action:  1
Frame Count:  368
Action:  4
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
Frame Count:  369
Action:  1
Frame Count:  370
Action:  1
Average Reward Across All Episodes:  0.0
Frame Count:  371
Action:  2
Frame Count:  372
Action:  4
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 21ms/step
Frame Count:  373
Action:  3
Frame Count:  374
Action:  0
Frame Count:  375
Action:  1
Frame Count:  376
Action:  2
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 21ms/step
Frame Count:  377
Action:  4
Frame Count:  378
Action:  4
Frame Count:  379
Action:  3
Frame Count:  380
Action:  1
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 22ms/step
Frame Count:  381
Action:  4
Frame Count:  382
Action:  1
Frame Count:  383
Action:  0
Frame Count:  384
Action:  1
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 21ms/st

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
Frame Count:  533
Action:  2
Frame Count:  534
Action:  3
Frame Count:  535
Action:  2
Frame Count:  536
Action:  1
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
Frame Count:  537
Action:  2
Frame Count:  538
Action:  4
Frame Count:  539
Action:  2
Frame Count:  540
Action:  4
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
Frame Count:  541
Action:  4
Frame Count:  542
Action:  4
Frame Count:  543
Action:  3
Frame Count:  544
Action:  3
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
Frame Count:  545
Action:  1
Frame Count:  546
Action:  0
Frame Count:  547
Action:  1
Frame Count:  548
Action:  3
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
Frame Count:  549
Action:  2
Frame Count:  550
Action:  1
Frame Count:  551
Action:  1
Frame Count:  552
Action:  0
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 13ms/step
Frame Count:  553
Action:  4
Frame Count:  554
Action:  0
Frame Count:  555
Action:  1
Frame Count:  556
Action:  4
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
Frame Count:  557
Action:  0
Frame Cou

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 26ms/step
Frame Count:  705
Action:  3
Frame Count:  706
Action:  2
Frame Count:  707
Action:  0
Frame Count:  708
Action:  4
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 24ms/step
Frame Count:  709
Action:  4
Frame Count:  710
Action:  2
Frame Count:  711
Action:  4
Frame Count:  712
Action:  1
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 28ms/step
Frame Count:  713
Action:  0
Frame Count:  714
Action:  4
Frame Count:  715
Action:  3
Frame Count:  716
Action:  3
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 25ms/step
Frame Count:  717
Action:  2
Frame Count:  718
Action:  2
Frame Count:  719
Action:  3
Frame Count:  720
Action:  2
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
Frame Count:  721
Action:  1
Frame Count:  722
Action:  3
Frame Count:  723
Action:  4
Frame Count:  724
Action:  2
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 25ms/step
Frame Count:  725
Action:  3
Frame Count:  726
Action:  1
Frame Count:  727
Action:  2
Frame Count:  728
Action:  2
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
Frame Count:  729
Action:  2
Frame Cou

...

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 64ms/step
Frame Count:  94505
Action:  4
Frame Count:  94506
tf.Tensor([[64.048546 64.05213  64.03207  64.011    63.931297]], shape=(1, 5), dtype=float32)
Action:  1
Frame Count:  94507
Action:  0
Frame Count:  94508
Action:  0
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 33ms/step
Frame Count:  94509
tf.Tensor([[68.66325  68.72784  68.854225 68.76344  68.90423 ]], shape=(1, 5), dtype=float32)
Action:  4
Frame Count:  94510
Action:  4
Frame Count:  94511
Action:  2
Frame Count:  94512
Action:  0
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 47ms/step
Frame Count:  94513
Action:  3
Frame Count:  94514
Action:  0
Frame Count:  94515
Action:  3
Frame Count:  94516
tf.Tensor([[54.695114 54.74963  54.797543 54.679222 54.80602 ]], shape=(1, 5), dtype=float32)
Action:  4
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
Frame Count:  94517
Action:  4
Frame Count:  94518
Action:  3
Frame Count:  94519
Action:  0
Frame Count:  94520
Action:  3
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 50ms/step
Frame Count:  94521
Action:  3
F

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 88ms/step
Frame Count:  94641
Action:  4
Frame Count:  94642
tf.Tensor([[62.518204 62.686462 62.911983 62.671295 62.98024 ]], shape=(1, 5), dtype=float32)
Action:  4
Frame Count:  94643
Action:  0
Frame Count:  94644
Action:  4
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 68ms/step
Frame Count:  94645
Action:  0
Frame Count:  94646
Action:  3
Average Reward Across All Episodes:  0.0
Frame Count:  94647
Action:  2
Frame Count:  94648
tf.Tensor([[63.508457 63.607376 63.534195 63.569942 63.692127]], shape=(1, 5), dtype=float32)
Action:  4
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 43ms/step
Frame Count:  94649
Action:  3
Frame Count:  94650
Action:  1
Frame Count:  94651
Action:  3
Frame Count:  94652
Action:  3
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 38ms/step
Frame Count:  94653
Action:  3
Frame Count:  94654
Action:  1
Frame Count:  94655
Action:  3
Frame Count:  94656
Action:  0
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 53ms/step
Frame Count:  94657
Action:  0
Frame Count:  94658
Action:  1
Frame Count:  94659
Act

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 46ms/step
Frame Count:  94785
Action:  2
Frame Count:  94786
Action:  4
Frame Count:  94787
Action:  4
Frame Count:  94788
Action:  0
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 36ms/step
Frame Count:  94789
tf.Tensor([[62.134113 62.184372 62.364418 62.332214 62.288635]], shape=(1, 5), dtype=float32)
Action:  2
Frame Count:  94790
Action:  4
Frame Count:  94791
Action:  3
Frame Count:  94792
Action:  1
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 47ms/step
Frame Count:  94793
Action:  1
Frame Count:  94794
Action:  0
Average Reward Across All Episodes:  0.0
Frame Count:  94795
Action:  0
Frame Count:  94796
tf.Tensor([[63.973125 63.987766 64.11357  64.22329  63.998425]], shape=(1, 5), dtype=float32)
Action:  3
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 54ms/step
Frame Count:  94797
Action:  3
Frame Count:  94798
Action:  2
Frame Count:  94799
Action:  1
Frame Count:  94800
Action:  2
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 44ms/step
Frame Count:  94801
Action:  2
Frame Count:  94802
Action:  0
Frame Count:  94803
Act

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 49ms/step
Frame Count:  94917
Action:  1
Frame Count:  94918
Action:  2
Frame Count:  94919
Action:  2
Frame Count:  94920
Action:  0
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 79ms/step
Frame Count:  94921
Action:  1
Frame Count:  94922
Action:  3
Frame Count:  94923
Action:  4
Frame Count:  94924
Action:  1
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 32ms/step
Frame Count:  94925
Action:  1
Frame Count:  94926
Action:  4
Frame Count:  94927
Action:  4
Frame Count:  94928
Action:  3
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 47ms/step
Frame Count:  94929
Action:  3
Frame Count:  94930
Action:  1
Frame Count:  94931
Action:  4
Frame Count:  94932
Action:  2
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 42ms/step
Frame Count:  94933
Action:  2
Frame Count:  94934
Action:  3
Frame Count:  94935
Action:  0
Frame Count:  94936
Action:  0
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 43ms/step
Frame Count:  94937
Action:  1
Frame Count:  94938
Action:  4
Frame Count:  94939
Action:  0
Frame Count:  94940
Action:  0
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 76ms/step
Frame Count:  95065
Action:  3
Frame Count:  95066
Action:  4
Frame Count:  95067
Action:  2
Frame Count:  95068
Action:  0
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 62ms/step
Frame Count:  95069
Action:  3
Frame Count:  95070
Action:  4
Frame Count:  95071
Action:  0
Frame Count:  95072
tf.Tensor([[63.22545  63.24866  63.33612  63.224224 63.340958]], shape=(1, 5), dtype=float32)
Action:  4
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 43ms/step
Frame Count:  95073
Action:  3
Frame Count:  95074
Action:  1
Frame Count:  95075
Action:  1
Frame Count:  95076
Action:  0
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 72ms/step
Frame Count:  95077
Action:  1
Frame Count:  95078
Action:  0
Frame Count:  95079
Action:  0
Frame Count:  95080
Action:  2
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 43ms/step
Frame Count:  95081
Action:  3
Frame Count:  95082
Action:  4
Frame Count:  95083
Action:  4
Frame Count:  95084
Action:  2
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 51ms/step
Frame Count:  95085
Action:  4
Frame Count:  95086
Action:

In [ ]:
cnn1.save_weights("cnn1v2.weights.h5") # Save the weights of each CNN
cnn2.save_weights("cnn2v2.weights.h5")

In [ ]:
model = create_CNN()
model.load_weights('cnn1v2.weights.h5')
env = gym.make('ALE/Frogger-v5', render_mode="human")
env = GrayscaleObservationV0(env)
env = FrameStack(env, 4) # Get 4 frames from game at a time
frames, width, height = env.observation_space.shape
env.reset()
game_over = False

In [ ]:
state, reward, game_over, x, _ = env.step(0)
while not game_over:
    
    #Predict action using the trained model
    q_values = model.predict(np.expand_dims(state, axis=0))
    action = np.argmax(q_values)

    # Take action in the environment
    next_state, reward, game_over, x, _ = env.step(action)

    # Update current state
    state = next_state